In [26]:
# import the required packages
import pandas as pd
import numpy as np
import re

# Visuals
import scipy.stats as stats
import matplotlib.pyplot as plt
import seaborn as sns
sns.set(style="white")
import matplotlib.dates as mdates
from datetime import datetime
import plotly.express as px

import nltk
from collections import Counter
from sklearn.preprocessing import StandardScaler, PolynomialFeatures, MinMaxScaler

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn import tree
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.svm import SVR
from xgboost import XGBRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

### M3_COM1_01

In [2]:
nov23 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_01/Ngee Ann Poly Solar Field_Nov23.xlsx')
dec23 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_01/Ngee Ann Poly Solar Field_Dec23.xlsx') 
jan24 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_01/Ngee Ann Poly Solar Field_Jan24.xlsx')
mar24 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_01/Ngee Ann Poly Solar Field_2Mar24.xlsx')
apr24 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_01/Ngee Ann Poly Solar Field_Apr24.xlsx')
may24 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_01/Ngee Ann Poly Solar Field_May24.xlsx')

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")
C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")
C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")
C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning: Workbook contains no default style, apply openpyxl's default
  warn("Workbook contains no default style, apply openpyxl's default")
C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles

In [3]:
nov23.head()

Unnamed: 0 2023-11-01 00:00 2023-11-01 00:05  \
0  30KTL-M3(COM1-1)_Active power(kW)               --               --   

  2023-11-01 00:10 2023-11-01 00:15 2023-11-01 00:20 2023-11-01 00:25  \
0               --               --               --               --   

  2023-11-01 00:30 2023-11-01 00:35 2023-11-01 00:40  ... 2023-11-30 23:15  \
0               --               --               --  ...               --   

  2023-11-30 23:20 2023-11-30 23:25 2023-11-30 23:30 2023-11-30 23:35  \
0               --               --               --               --   

  2023-11-30 23:40 2023-11-30 23:45 2023-11-30 23:50 2023-11-30 23:55  \
0               --               --               --               --   

  2023-12-01 00:00  
0               --  

[1 rows x 8642 columns]

In [4]:
def transform_df(df):
    # transpose to change row to columns within data
    # iloc[1:] to rid off the first row
    df = df.transpose().iloc[1:]
    # iloc[:-1] to ridd off the last row
    df=df.iloc[:-1]
    # reset index to retrieve datatime from index
    df.reset_index(inplace=True)
    # rename columns
    df.rename(columns={'index':'datetime',0:'kW'},inplace=True)
    
    return df

In [5]:
dataframes = [nov23,dec23,jan24,mar24,apr24,may24]
dataframes = [transform_df(df) for df in dataframes]
nov23,dec23,jan24,mar24,apr24,may24 = dataframes

In [6]:
# data are collected in intervals of 5 mins, each day theres 288 of 5 minutes
print(len(nov23)==(288*30))
print(len(dec23)==(288*31))
print(len(jan24)==(288*31))
print(len(mar24)==(288*31))
print(len(apr24)==(288*30))
print(len(may24)==(288*31))

True
True
True
True
True
True


In [7]:
nov23.info()
print(nov23.iloc[1])

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8640 entries, 0 to 8639
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   datetime  8640 non-null   object
 1   kW        8640 non-null   object
dtypes: object(2)
memory usage: 135.1+ KB
datetime    2023-11-01 00:05
kW                        --
Name: 1, dtype: object


In [8]:
dataframes = [nov23,dec23,jan24,mar24,apr24,may24]
names = ["Nov 23","Dec 23","Jan 24","Mar 24","Apr 24","May 24"]
for df in dataframes:
    df.replace("--",0.0,inplace=True)
    df['datetime'] = pd.to_datetime(df['datetime'])

In [20]:
for name, df in zip(names,dataframes):
    print("Name:",name)
    print("Dataframe Shape:",df.shape)
    print("Correct dtype?:",df['datetime'].dtype=='datetime64[ns]' and df['kW'].dtype=='float64')

Name: nov23
Dataframe Shape: (8640, 2)
Correct dtype?: True
Name: dec23
Dataframe Shape: (8928, 2)
Correct dtype?: True
Name: jan24
Dataframe Shape: (8928, 2)
Correct dtype?: True
Name: mar24
Dataframe Shape: (8928, 2)
Correct dtype?: True
Name: apr24
Dataframe Shape: (8640, 2)
Correct dtype?: True
Name: may24
Dataframe Shape: (8928, 2)
Correct dtype?: True


In [37]:
for name, df in zip(names,dataframes):

    fig=px.line(df, x='datetime',y='kW',title=f"Solar Power Output Over Time for {name}",
               template="plotly_dark")
    fig.show()

In [44]:
for name,df in zip(names,dataframes):
    print(name)
    daily_sum = df.groupby(df['datetime'].dt.date)['kW'].sum().sort_values(ascending=False)
    print((daily_sum[daily_sum!=0].sort_values(ascending=False)).head())

Nov 23
datetime
2023-11-30    1267.11
2023-11-29     453.68
Name: kW, dtype: float64
Dec 23
datetime
2023-12-15    1834.88
2023-12-05    1703.21
2023-12-29    1633.49
2023-12-08    1539.44
2023-12-18    1519.34
Name: kW, dtype: float64
Jan 24
datetime
2024-01-02    1594.07
2024-01-08    1455.00
2024-01-05    1304.79
2024-01-06    1294.28
2024-01-03    1152.88
Name: kW, dtype: float64
Mar 24
datetime
2024-03-26    2537.98
2024-03-18    2466.42
2024-03-25    2382.92
2024-03-27    2375.13
2024-03-12    2266.55
Name: kW, dtype: float64
Apr 24
datetime
2024-04-29    2255.43
2024-04-18    2193.53
2024-04-24    2107.23
2024-04-02    2105.02
2024-04-09    2103.39
Name: kW, dtype: float64
May 24
datetime
2024-05-02    1573.02
2024-05-01    1485.53
2024-05-03    1364.86
2024-05-05     907.84
2024-05-04     387.70
Name: kW, dtype: float64


In [46]:
for name,df in zip(names,dataframes):
    print(name)
    avg_power_over_time = df.groupby(df['datetime'].dt.time)['kW'].mean().sort_values(ascending=False)
    print((avg_power_over_time).round(2).head())

Nov 23
datetime
13:25:00    1.1
13:10:00    1.1
13:20:00    1.1
13:50:00    1.1
13:55:00    1.1
Name: kW, dtype: float64
Dec 23
datetime
11:00:00    18.02
13:10:00    17.70
11:05:00    17.61
12:05:00    17.25
12:50:00    17.21
Name: kW, dtype: float64
Jan 24
datetime
12:35:00    5.17
14:20:00    4.95
12:55:00    4.61
12:20:00    4.60
12:40:00    4.52
Name: kW, dtype: float64
Mar 24
datetime
11:35:00    25.37
11:45:00    24.62
11:40:00    24.22
11:55:00    23.92
11:50:00    23.77
Name: kW, dtype: float64
Apr 24
datetime
13:45:00    23.31
13:15:00    22.15
14:05:00    22.13
12:50:00    21.79
14:00:00    21.17
Name: kW, dtype: float64
May 24
datetime
11:55:00    3.86
11:50:00    3.48
13:45:00    3.44
13:25:00    3.38
10:15:00    3.28
Name: kW, dtype: float64


### M3_COM1_02

In [47]:
nov23_1 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_02/Ngee Ann Poly Solar Field_Nov23.xlsx')
dec23_1 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_02/Ngee Ann Poly Solar Field_Dec23.xlsx') 
jan24_1 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_02/Ngee Ann Poly Solar Field_Jan24.xlsx')
mar24_1 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_02/Ngee Ann Poly Solar Field_Mar24.xlsx')
apr24_1 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_02/Ngee Ann Poly Solar Field_Apr24.xlsx')
may24_1 = pd.read_excel('ASG2 & beyond/SOE Solar Datasets/M3_COM1_02/Ngee Ann Poly Solar Field_May24.xlsx')

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default

C:\Users\Cheong Chun Fai\anaconda3\lib\site-packages\openpyxl\styles\stylesheet.py:226: UserWarning:

Workbook contains no default style, apply openpyxl's default



In [48]:
dataframes_1 = [nov23_1,dec23_1,jan24_1,mar24_1,apr24_1,may24_1]
dataframes_1 = [transform_df(df) for df in dataframes_1]
nov23_1,dec23_1,jan24_1,mar24_1,apr24_1,may24_1 = dataframes_1

In [49]:
print(len(nov23_1)==(288*30))
print(len(dec23_1)==(288*31))
print(len(jan24_1)==(288*31))
print(len(mar24_1)==(288*31))
print(len(apr24_1)==(288*30))
print(len(may24_1)==(288*31))

True
True
True
True
True
True


In [51]:
nov23_1.info()
print(nov23_1.iloc[1])

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8640 entries, 0 to 8639
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   datetime  8640 non-null   object
 1   kW        8640 non-null   object
dtypes: object(2)
memory usage: 135.1+ KB
datetime    2023-11-01 00:05
kW                        --
Name: 1, dtype: object


In [52]:
dataframes_1 = [nov23_1,dec23_1,jan24_1,mar24_1,apr24_1,may24_1]
names = ["Nov 23","Dec 23","Jan 24","Mar 24","Apr 24","May 24"]
for df in dataframes_1:
    df.replace("--",0.0,inplace=True)
    df['datetime'] = pd.to_datetime(df['datetime'])

In [53]:
for name, df in zip(names,dataframes_1):
    print("Name:",name)
    print("Dataframe Shape:",df.shape)
    print("Correct dtype?:",df['datetime'].dtype=='datetime64[ns]' and df['kW'].dtype=='float64')

Name: Nov 23
Dataframe Shape: (8640, 2)
Correct dtype?: True
Name: Dec 23
Dataframe Shape: (8928, 2)
Correct dtype?: True
Name: Jan 24
Dataframe Shape: (8928, 2)
Correct dtype?: True
Name: Mar 24
Dataframe Shape: (8928, 2)
Correct dtype?: True
Name: Apr 24
Dataframe Shape: (8640, 2)
Correct dtype?: True
Name: May 24
Dataframe Shape: (8928, 2)
Correct dtype?: True


In [54]:
for name, df in zip(names,dataframes_1):

    fig=px.line(df, x='datetime',y='kW',title=f"Solar Power Output Over Time for {name}",
               template="plotly_dark")
    fig.show()

In [55]:
for name,df in zip(names,dataframes_1):
    print(name)
    daily_sum = df.groupby(df['datetime'].dt.date)['kW'].sum().sort_values(ascending=False)
    print((daily_sum[daily_sum!=0].sort_values(ascending=False)).head())

Nov 23
datetime
2023-11-30    930.71
2023-11-29    353.42
Name: kW, dtype: float64
Dec 23
datetime
2023-12-15    1266.23
2023-12-29    1212.79
2023-12-05    1212.62
2023-12-22    1121.34
2023-12-08    1113.26
Name: kW, dtype: float64
Jan 24
datetime
2024-01-02    1147.91
2024-01-08    1043.19
2024-01-05     966.29
2024-01-06     952.64
2024-01-03     836.46
Name: kW, dtype: float64
Mar 24
datetime
2024-03-18    1861.99
2024-03-26    1846.77
2024-03-24    1808.28
2024-03-25    1752.69
2024-03-27    1744.69
Name: kW, dtype: float64
Apr 24
datetime
2024-04-29    1636.99
2024-04-18    1568.46
2024-04-09    1536.38
2024-04-02    1532.80
2024-04-06    1500.92
Name: kW, dtype: float64
May 24
datetime
2024-05-01    1285.88
2024-05-02    1152.72
2024-05-03    1032.86
2024-05-05     764.05
2024-05-04     283.61
Name: kW, dtype: float64


In [56]:
for name,df in zip(names,dataframes_1):
    print(name)
    avg_power_over_time = df.groupby(df['datetime'].dt.time)['kW'].mean().sort_values(ascending=False)
    print((avg_power_over_time).round(2).head())

Nov 23
datetime
12:40:00    0.82
12:20:00    0.81
11:50:00    0.81
13:55:00    0.80
13:50:00    0.78
Name: kW, dtype: float64
Dec 23
datetime
11:05:00    13.04
13:00:00    12.75
12:05:00    12.62
11:00:00    12.60
13:10:00    12.56
Name: kW, dtype: float64
Jan 24
datetime
12:35:00    3.54
12:55:00    3.26
14:35:00    3.22
12:20:00    3.21
13:05:00    3.16
Name: kW, dtype: float64
Mar 24
datetime
11:50:00    19.20
12:05:00    18.72
11:45:00    18.69
11:35:00    18.55
11:55:00    18.44
Name: kW, dtype: float64
Apr 24
datetime
12:50:00    17.04
12:40:00    16.68
13:45:00    16.23
13:15:00    16.17
13:00:00    15.84
Name: kW, dtype: float64
May 24
datetime
13:45:00    2.64
11:55:00    2.62
12:05:00    2.52
11:50:00    2.52
10:15:00    2.44
Name: kW, dtype: float64
